# A. Libraries

In [30]:
import sys
sys.path.append('..')
import numpy as np
import pandas as pd
import time
from datetime import datetime, timedelta, timezone
import datetime
import os
import matplotlib.pyplot as plt
import seaborn as sns
import notebooks.force_defs as force_defs
import math
import importlib
importlib.reload(force_defs)
import glob
import re


# B. RFID

### 1. append all the data files

In [17]:
#latest run: 2025-04-18

folder_path = 'C:\\Users\\kmh\\Documents\\DATA\\2024-5\\RFID\\RFID\\1day_before'  # Replace with your folder path
output_file = 'RFID_day-1.csv'  # Replace with your desired output file name

#folder_path2 = 'C:\\Users\\kmh\\Documents\\DATA\\2024-5\\RFID\\SCARE'
#output_file2 = 'SCARE_24Dec11_28.csv'

defs.append_csv_files(folder_path, output_file) 
#append_csv_files(folder_path2, output_file2)


In [19]:
RFID_dayminus1 = pd.read_csv('RFID_day-1.csv')
print(RFID_dayminus1.head(5))
print(RFID_dayminus1['date'].unique())


           id  status        date             time    epoch_time location
0  3B00185E23  Arrive  2024-12-11  08:59:35:920756  1.733900e+15     RFID
1  3B00185E23  Depart  2024-12-11  08:59:38:329956  1.733900e+15     RFID
2  3B0018C6F9  Arrive  2024-12-11  09:00:47:726152  1.733900e+15     RFID
3  3B0018C6F9  Depart  2024-12-11  09:00:50:939834  1.733900e+15     RFID
4  3B00185E23  Arrive  2024-12-11  09:02:36:441403  1.733900e+15     RFID
['2024-12-11' nan '2024-12-14' '2024-12-22' '2024-12-30' '2025-01-02'
 '2025-01-20' '2025-01-23' '2025-01-29' '2025-02-05' '2025-02-11'
 '2025-02-15' '2025-02-18']


### 2. datetime formatting

#### method A - brute force - just for 2025-02-16 & 17
- for all of RFID_dayminus1 and RFID_day1

In [20]:
RFID_dayminus1['time'] = RFID_dayminus1['time'].astype(str).apply(lambda x: ".".join(x.rsplit(":", 1)))
RFID_dayminus1['datetime'] = RFID_dayminus1['date']+ ' '+RFID_dayminus1['time']
RFID_dayminus1['datetime'] = pd.to_datetime(RFID_dayminus1['datetime'])
#-1hr 
RFID_dayminus1['rfid_datetime'] = RFID_dayminus1['datetime'] - pd.to_timedelta(1, unit='h')

RFID_dayminus1.head(3)
#amazing. Looking good! 

id  status        date             time    epoch_time location  \
0  3B00185E23  Arrive  2024-12-11  08:59:35.920756  1.733900e+15     RFID   
1  3B00185E23  Depart  2024-12-11  08:59:38.329956  1.733900e+15     RFID   
2  3B0018C6F9  Arrive  2024-12-11  09:00:47.726152  1.733900e+15     RFID   

                    datetime              rfid_datetime  
0 2024-12-11 08:59:35.920756 2024-12-11 07:59:35.920756  
1 2024-12-11 08:59:38.329956 2024-12-11 07:59:38.329956  
2 2024-12-11 09:00:47.726152 2024-12-11 08:00:47.726152

#### method B. calculating from epoch_time to see it matches

In [9]:
RFID = pd.read_csv('RFID_day-1.csv')
print(RFID.head(3))
print(RFID.dtypes)

# Apply the function to the 'epoch_time' column, handling NaN values
RFID['rfid_datetime'] = RFID['epoch_time'].apply(lambda x: defs.convert_time_rfid(x) if pd.notnull(x) else None)

# Print the DataFrame with the new epoch_time_converted column
print(RFID.shape)
print(RFID.head(5))


           id  status        date             time    epoch_time location
0  3B00185E23  Arrive  2024-12-11  08:59:35:920756  1.733904e+15     RFID
1  3B00185E23  Depart  2024-12-11  08:59:38:329956  1.733904e+15     RFID
2  3B0018C6F9  Arrive  2024-12-11  09:00:47:726152  1.733904e+15     RFID
id             object
status         object
date           object
time           object
epoch_time    float64
location       object
dtype: object
(15422, 7)
           id  status        date             time    epoch_time location  \
0  3B00185E23  Arrive  2024-12-11  08:59:35:920756  1.733904e+15     RFID   
1  3B00185E23  Depart  2024-12-11  08:59:38:329956  1.733904e+15     RFID   
2  3B0018C6F9  Arrive  2024-12-11  09:00:47:726152  1.733904e+15     RFID   
3  3B0018C6F9  Depart  2024-12-11  09:00:50:939834  1.733904e+15     RFID   
4  3B00185E23  Arrive  2024-12-11  09:02:36:441403  1.733904e+15     RFID   

                rfid_datetime  
0  2024-12-11 07:59:35:920756  
1  2024-12-11 07:59:

##### consolidation & concatenation
- and add Feb16 then 

In [21]:
#dataset of interest
RFID = RFID_dayminus1

In [22]:
#selecting specific columns 
RFID_match = RFID[['id','status','rfid_datetime']]
RFID_match2 = RFID_match
print(f"RFID_match2 shape: {RFID_match2.shape}")
print(RFID_match2.head(3))
print(RFID_match2.dtypes)

#make sure RFID_match2 is in datetime before adding with Feb17 
RFID_match2['rfid_datetime'] =pd.to_datetime(RFID_match2['rfid_datetime'], format = '%Y-%m-%d %H:%M:%S:%f')
print(RFID_match2.dtypes)
print(RFID_match2.head(3))



RFID_match2 shape: (15422, 3)
           id  status              rfid_datetime
0  3B00185E23  Arrive 2024-12-11 07:59:35.920756
1  3B00185E23  Depart 2024-12-11 07:59:38.329956
2  3B0018C6F9  Arrive 2024-12-11 08:00:47.726152
id                       object
status                   object
rfid_datetime    datetime64[ns]
dtype: object
id                       object
status                   object
rfid_datetime    datetime64[ns]
dtype: object
           id  status              rfid_datetime
0  3B00185E23  Arrive 2024-12-11 07:59:35.920756
1  3B00185E23  Depart 2024-12-11 07:59:38.329956
2  3B0018C6F9  Arrive 2024-12-11 08:00:47.726152


In [62]:
# adding problematic Feb16

Feb_match = Feb17[['id','status','rfid_datetime']]

print(f"RFID_match.shape: {RFID_match.shape}")

#concatenating Feb16 and RFID_match
RFID_match2 = pd.concat([RFID_match, Feb_match], ignore_index=True)

print(f"after concatenation - RFID_match2: {RFID_match2.shape}")
print(RFID_match2.head(3))


RFID_match.shape: (8873, 3)
after concatenation - RFID_match2: (9150, 3)
           id  status              rfid_datetime
0  3B00190DF0  Arrive 2024-12-13 09:07:04.359618
1  3B00190DF0  Depart 2024-12-13 09:07:06.771829
2  3B00185E23  Arrive 2024-12-13 09:20:00.998900


In [23]:
RFID_match2['rfid_datetime'] = pd.to_datetime(RFID_match2['rfid_datetime'], errors = 'coerce')
RFID_match3 = RFID_match2.sort_values(by='rfid_datetime')
RFID_match4 = RFID_match3.reset_index(drop=True)
print(f"matched: {RFID_match4.shape}") #12380
print(RFID_match4.head(3))

matched: (15422, 3)
           id  status              rfid_datetime
0  3B00185E23  Arrive 2024-12-11 07:59:35.920756
1  3B00185E23  Depart 2024-12-11 07:59:38.329956
2  3B0018C6F9  Arrive 2024-12-11 08:00:47.726152


### filter this so that all 'id' column is 10 characters long and none of the characters are '?'.

In [24]:
RFID_match4.columns
RFID_match4.loc[:, 'id'] = RFID_match4['id'].astype(str)
RFID_match5 = RFID_match4[(RFID_match4['id'].str.len() == 10) 
                        & (~RFID_match4['id'].str.contains('?', regex=False))]

RFID_match5.shape


(15290, 3)

In [25]:
RFID_match5.to_csv('RFID_match_day-1.csv') #used method A to re-make RFID_match_day1

# C. IR

### 1. append all the .txt data files to csv

In [84]:
#latest run 2025-05-08
import os
import pandas as pd

def append_text_files(folder_path, output_file):
    combined_df = pd.DataFrame()  # Initialize an empty DataFrame

    for filename in os.listdir(folder_path):  # Iterate through each file in the specified folder
        if filename.endswith('.txt'):  # Check if the file has a .txt extension
            file_path = os.path.join(folder_path, filename)  # Construct the full file path
            df = pd.read_csv(file_path, delimiter='\t')  # Read the text file into a DataFrame with tab delimiter

            if combined_df.empty:  # If the combined DataFrame is empty, initialize it with the first DataFrame
                combined_df = df
            else:
                if list(combined_df.columns) == list(df.columns):  # Check if the column names are the same
                    combined_df = pd.concat([combined_df, df], ignore_index=True)  # Append the rows

    combined_df.to_csv(output_file, index=False, sep='\t')  # Write the combined DataFrame to the output file with tab delimiter

# Example usage
folder_path = 'C:\\Users\\kmh\\Documents\\DATA\\2024-5\\IR\\1day_before' 
output_file = 'IR_-1day.csv' 
append_text_files(folder_path, output_file)



In [150]:
IR = pd.read_csv('IR_-1day.csv',dtype ={'Sensor':int, 'Time':float}, sep =',')
IR.head(10)

Sensor          Time
0       5  1.733904e+12
1       5  1.733904e+12
2       5  1.733904e+12
3       4  1.733904e+12
4       4  1.733904e+12
5       3  1.733904e+12
6       5  1.733904e+12
7       3  1.733904e+12
8       2  1.733904e+12
9       4  1.733904e+12

### 2. convert to datetime format

In [ ]:
# Apply the function to the 'epoch_time' column, handling NaN values
IR['datetime'] = IR['Time'].apply(lambda x: force_defs.convert_time_IR(x) if pd.notnull(x) else None)

# Print the DataFrame with the new epoch_time_converted column
print(IR.head(10))
print(IR.dtypes)

   Sensor          Time                    datetime
0       5  1.733904e+12  2024-12-11 07:59:33:874000
1       5  1.733904e+12  2024-12-11 07:59:33:885000
2       5  1.733904e+12  2024-12-11 07:59:33:874000
3       4  1.733904e+12  2024-12-11 07:59:33:930000
4       4  1.733904e+12  2024-12-11 07:59:33:943000
5       3  1.733904e+12  2024-12-11 07:59:33:983000
6       5  1.733904e+12  2024-12-11 07:59:33:936000
7       3  1.733904e+12  2024-12-11 07:59:33:998000
8       2  1.733904e+12  2024-12-11 07:59:34:061000
9       4  1.733904e+12  2024-12-11 07:59:34:008000
Sensor        int32
Time        float64
datetime     object
dtype: object


In [152]:
# Convert 'datetime' column to datetime type for easier manipulation and filtering
IR['Sensor'] = IR['Sensor'].astype(str)
IR['datetime'] = pd.to_datetime(IR['datetime'], format='%Y-%m-%d %H:%M:%S:%f')
print(IR.shape) #192872
IR_unique = IR.drop_duplicates()
print(IR_unique.shape)
print(IR_unique.head(10))
print(IR_unique.dtypes)
print(IR_unique.columns)
print(type(IR_unique))
IR_unique['Sensor'] =IR_unique['Sensor'].astype(int)
print(IR_unique.dtypes)


(258317, 3)
(253676, 3)
   Sensor          Time                datetime
0       5  1.733904e+12 2024-12-11 07:59:33.874
1       5  1.733904e+12 2024-12-11 07:59:33.885
3       4  1.733904e+12 2024-12-11 07:59:33.930
4       4  1.733904e+12 2024-12-11 07:59:33.943
5       3  1.733904e+12 2024-12-11 07:59:33.983
6       5  1.733904e+12 2024-12-11 07:59:33.936
7       3  1.733904e+12 2024-12-11 07:59:33.998
8       2  1.733904e+12 2024-12-11 07:59:34.061
9       4  1.733904e+12 2024-12-11 07:59:34.008
10      3  1.733904e+12 2024-12-11 07:59:34.080
Sensor              object
Time               float64
datetime    datetime64[ns]
dtype: object
Index(['Sensor', 'Time', 'datetime'], dtype='object')
<class 'pandas.core.frame.DataFrame'>
Sensor               int32
Time               float64
datetime    datetime64[ns]
dtype: object


### 3. 12345 sequence filter

#### a. filtering 12345 sequence

In [153]:
import pandas as pd

# Define the sequence to filter
sequence = [1, 2, 3, 4, 5]

# Find and filter the sequence
filtered_IR_Sensor = defs.find_and_filter_sequence(IR_unique, sequence)
#filtered_IR_Sensor: full dataset with 'Sensor' column filtered

# Display the filtered DataFrame A
print(filtered_IR_Sensor.head(10))
print(filtered_IR_Sensor.shape)

     Sensor          Time                datetime  takeoff_event
134       1  1.733904e+12 2024-12-11 08:00:48.289              1
136       1  1.733904e+12 2024-12-11 08:00:48.352              1
137       1  1.733904e+12 2024-12-11 08:00:48.356              1
138       1  1.733904e+12 2024-12-11 08:00:48.419              1
140       2  1.733904e+12 2024-12-11 08:00:48.572              1
142       2  1.733904e+12 2024-12-11 08:00:48.636              1
143       2  1.733904e+12 2024-12-11 08:00:48.641              1
144       3  1.733904e+12 2024-12-11 08:00:48.703              1
145       3  1.733904e+12 2024-12-11 08:00:48.713              1
146       4  1.733904e+12 2024-12-11 08:00:48.761              1
(111490, 4)


In [154]:


# Use the indices to filter the matching rows in the original dataset
filtered_df = filtered_IR_Sensor.drop_duplicates().sort_values(by = 'datetime').reset_index()

print(filtered_df.shape)
print(filtered_df.head(20))
print(filtered_df.dtypes)


(111490, 5)
    index  Sensor          Time                datetime  takeoff_event
0     134       1  1.733904e+12 2024-12-11 08:00:48.289              1
1     136       1  1.733904e+12 2024-12-11 08:00:48.352              1
2     137       1  1.733904e+12 2024-12-11 08:00:48.356              1
3     138       1  1.733904e+12 2024-12-11 08:00:48.419              1
4     140       2  1.733904e+12 2024-12-11 08:00:48.572              1
5     142       2  1.733904e+12 2024-12-11 08:00:48.636              1
6     143       2  1.733904e+12 2024-12-11 08:00:48.641              1
7     144       3  1.733904e+12 2024-12-11 08:00:48.703              1
8     145       3  1.733904e+12 2024-12-11 08:00:48.713              1
9     146       4  1.733904e+12 2024-12-11 08:00:48.761              1
10    147       4  1.733904e+12 2024-12-11 08:00:48.780              1
11    148       5  1.733904e+12 2024-12-11 08:00:48.828              1
12    149       5  1.733904e+12 2024-12-11 08:00:48.848          

#### b. isolated take-off events e.g. no 5 logs from other birds. 

In [155]:

# Apply the function and show the result
final_filtered_df = defs.isolate_takeoff(filtered_df)


In [156]:
print("\nFiltered DataFrame:")
print(final_filtered_df.head(20)) #oooh so well filtered! #38:51



Filtered DataFrame:
    level_0  index  Sensor          Time                datetime  \
0         0    134       1  1.733904e+12 2024-12-11 08:00:48.289   
1         1    136       1  1.733904e+12 2024-12-11 08:00:48.352   
2         2    137       1  1.733904e+12 2024-12-11 08:00:48.356   
3         3    138       1  1.733904e+12 2024-12-11 08:00:48.419   
4         4    140       2  1.733904e+12 2024-12-11 08:00:48.572   
5         5    142       2  1.733904e+12 2024-12-11 08:00:48.636   
6         6    143       2  1.733904e+12 2024-12-11 08:00:48.641   
7         7    144       3  1.733904e+12 2024-12-11 08:00:48.703   
8         8    145       3  1.733904e+12 2024-12-11 08:00:48.713   
9         9    146       4  1.733904e+12 2024-12-11 08:00:48.761   
10       10    147       4  1.733904e+12 2024-12-11 08:00:48.780   
11       11    148       5  1.733904e+12 2024-12-11 08:00:48.828   
12       12    149       5  1.733904e+12 2024-12-11 08:00:48.848   
22       22    284       1 

In [157]:
final_filtered_df.shape

(80603, 6)

In [94]:
final_filtered_df.to_csv('final_filtered_IR_day-1.csv')

# D. RFID - IR marry


### IR dataset

In [158]:
final_filtered_df = pd.read_csv('final_filtered_IR_day-1.csv', index_col = 0)
# Convert 'datetime' column to datetime type for easier manipulation and filtering
final_filtered_df['Sensor'] = final_filtered_df['Sensor'].astype(str)
final_filtered_df['datetime'] = pd.to_datetime(final_filtered_df['datetime'], format='%Y-%m-%d %H:%M:%S.%f')
print(final_filtered_df.shape)
print(final_filtered_df.head(5))
print(final_filtered_df.dtypes)
print(type(final_filtered_df))

(80603, 6)
   level_0  index Sensor          Time                datetime  takeoff_event
0        0    134      1  1.733904e+12 2024-12-11 08:00:48.289              1
1        1    136      1  1.733904e+12 2024-12-11 08:00:48.352              1
2        2    137      1  1.733904e+12 2024-12-11 08:00:48.356              1
3        3    138      1  1.733904e+12 2024-12-11 08:00:48.419              1
4        4    140      2  1.733904e+12 2024-12-11 08:00:48.572              1
level_0                   int64
index                     int64
Sensor                   object
Time                    float64
datetime         datetime64[ns]
takeoff_event             int64
dtype: object
<class 'pandas.core.frame.DataFrame'>


### RFID dataset

In [160]:
RFID_match = pd.read_csv('RFID_match_day-1.csv', index_col = 0 )
#id to string
RFID_match['id'] = RFID_match['id'].astype(str)
#datetime format conversion
RFID_match['rfid_datetime'] = pd.to_datetime(RFID_match['rfid_datetime'], format='%Y-%m-%d %H:%M:%S.%f')

print(f"RFID_match shape: {RFID_match.shape}")
print(RFID_match.dtypes)
print(type(RFID_match))


RFID_match shape: (15290, 3)
id                       object
status                   object
rfid_datetime    datetime64[ns]
dtype: object
<class 'pandas.core.frame.DataFrame'>


In [161]:
print(RFID_match.head(5))
RFID_match['day'] = RFID_match['rfid_datetime'].dt.date
RFID_match['day'].unique() #02-16 for day0 & 02-17 for day1 in 

           id  status              rfid_datetime
0  3B00185E23  Arrive 2024-12-11 07:59:35.920756
1  3B00185E23  Depart 2024-12-11 07:59:38.329956
2  3B0018C6F9  Arrive 2024-12-11 08:00:47.726152
3  3B0018C6F9  Depart 2024-12-11 08:00:50.939834
4  3B00185E23  Arrive 2024-12-11 08:02:36.441403


array([datetime.date(2024, 12, 11), datetime.date(2024, 12, 14),
       datetime.date(2024, 12, 22), datetime.date(2024, 12, 30),
       datetime.date(2025, 1, 2), datetime.date(2025, 1, 20),
       datetime.date(2025, 1, 23), datetime.date(2025, 1, 29),
       datetime.date(2025, 2, 5), datetime.date(2025, 2, 11),
       datetime.date(2025, 2, 15), datetime.date(2025, 2, 18)],
      dtype=object)

In [162]:
final_filtered_df['day'] = final_filtered_df['datetime'].dt.date
final_filtered_df.head(5)
final_filtered_df['day'].unique() #02-16 in. 

array([datetime.date(2024, 12, 11), datetime.date(2024, 12, 14),
       datetime.date(2024, 12, 22), datetime.date(2024, 12, 30),
       datetime.date(2025, 1, 2), datetime.date(2025, 1, 20),
       datetime.date(2025, 1, 23), datetime.date(2025, 1, 29),
       datetime.date(2025, 2, 5), datetime.date(2025, 2, 11),
       datetime.date(2025, 2, 15), datetime.date(2025, 2, 18)],
      dtype=object)

In [ ]:
#each takeoff_event has to be matched with a RFID

### group by takeoff_event

In [163]:

#for each unique value in the column 'takeoff_event', find the first index value in the column 'Sensor'. 
first_sensor_for_event = final_filtered_df.groupby('takeoff_event')['datetime'].first()

print(first_sensor_for_event.head(3))

#changing the series to dataframe
takeoff_match = first_sensor_for_event.reset_index().rename(columns={'index': 'takeoff no.'})

#setting 'RFID' column with NAs
takeoff_match['RFID'] = pd.NA

#making day column 
takeoff_match['day'] = takeoff_match['datetime'].dt.date
takeoff_match.head(5)
takeoff_match['day'].unique() 

range(len(RFID_match))


takeoff_event
1   2024-12-11 08:00:48.289
2   2024-12-11 08:02:31.780
3   2024-12-11 08:02:36.599
Name: datetime, dtype: datetime64[ns]


range(0, 15290)

In [ ]:
takeoff_match.to_csv('takeoff_match_day-1.csv')
RFID_match.to_csv('RFID_match_day-1.csv')

In [164]:
RFID_match['day'].unique()

array([datetime.date(2024, 12, 11), datetime.date(2024, 12, 14),
       datetime.date(2024, 12, 22), datetime.date(2024, 12, 30),
       datetime.date(2025, 1, 2), datetime.date(2025, 1, 20),
       datetime.date(2025, 1, 23), datetime.date(2025, 1, 29),
       datetime.date(2025, 2, 5), datetime.date(2025, 2, 11),
       datetime.date(2025, 2, 15), datetime.date(2025, 2, 18)],
      dtype=object)

### match RFID and IR

somehow the code below returns an empty dataframe. final_filtered_df is good and RFID_match is also good but cannot match the two. 
Same issue 2025-04-04 
- on 2025-04-04 the code worked starting from libraries -> IR dataset -> RFID datset -> then matching. 

### without parallel processing 

In [165]:

import pandas as pd
from tqdm import tqdm

# Function to process each row
def process_row(i):
    print(f"Processing row: {i}")
    if RFID_match['status'].iloc[i] == "Arrive" and RFID_match['status'].iloc[i + 1] in ["Displace", "Depart"]:
        arrival_time = RFID_match['rfid_datetime'].iloc[i]
        depart_time = RFID_match['rfid_datetime'].iloc[i + 1]
        arrival_RFID = RFID_match['id'].iloc[i]
        #print(f"Arrive found at row {i} with RFID {arrival_RFID} from {arrival_time} to {depart_time}")

        # Vectorized operation to assign RFID
        mask = (takeoff_match['datetime'] > arrival_time) & (takeoff_match['datetime'] < depart_time)
        takeoff_match.loc[mask, 'RFID'] = arrival_RFID
        print(f"Assigned RFID {arrival_RFID} to {mask.sum()} rows in takeoff_match")

    elif RFID_match['status'].iloc[i] == "Displace" and RFID_match['status'].iloc[i + 1] == "Depart":
        arrival_time = RFID_match['rfid_datetime'].iloc[i]
        depart_time = RFID_match['rfid_datetime'].iloc[i + 1]
        arrival_RFID = RFID_match['id'].iloc[i]
        #print(f"Displace found at row {i} with RFID {arrival_RFID} from {arrival_time} to {depart_time}")

        # Vectorized operation to assign RFID
        mask = (takeoff_match['datetime'] > arrival_time) & (takeoff_match['datetime'] < depart_time)
        takeoff_match.loc[mask, 'RFID'] = arrival_RFID
        print(f"Assigned RFID {arrival_RFID} to {mask.sum()} rows in takeoff_match")

# Process rows sequentially
for i in tqdm(range(len(RFID_match) - 1)):
    process_row(i) #just 6.4 rows



  3%|▎         | 508/15289 [00:00<00:02, 5069.08it/s]

Processing row: 0
Assigned RFID 3B00185E23 to 0 rows in takeoff_match
Processing row: 1
Processing row: 2
Assigned RFID 3B0018C6F9 to 1 rows in takeoff_match
Processing row: 3
Processing row: 4
Assigned RFID 3B00185E23 to 1 rows in takeoff_match
Processing row: 5
Processing row: 6
Assigned RFID 3B00199DE5 to 0 rows in takeoff_match
Processing row: 7
Processing row: 8
Assigned RFID 3B00185CB8 to 0 rows in takeoff_match
Processing row: 9
Processing row: 10
Assigned RFID 3B00185CB8 to 2 rows in takeoff_match
Processing row: 11
Processing row: 12
Assigned RFID 3B0018C6F9 to 0 rows in takeoff_match
Processing row: 13
Processing row: 14
Assigned RFID 01103FA4B2 to 1 rows in takeoff_match
Processing row: 15
Processing row: 16
Assigned RFID 3B0019B8CC to 0 rows in takeoff_match
Processing row: 17
Processing row: 18
Assigned RFID 3B00185CB8 to 1 rows in takeoff_match
Processing row: 19
Processing row: 20
Assigned RFID 3B00190DF0 to 1 rows in takeoff_match
Processing row: 21
Processing row: 22
A

 10%|▉         | 1515/15289 [00:00<00:02, 4826.73it/s]

Assigned RFID 01103F97C4 to 0 rows in takeoff_match
Processing row: 965
Processing row: 966
Assigned RFID 3B00190DF0 to 0 rows in takeoff_match
Processing row: 967
Processing row: 968
Assigned RFID 3B0019B8CC to 0 rows in takeoff_match
Processing row: 969
Processing row: 970
Assigned RFID 3B00185E23 to 0 rows in takeoff_match
Processing row: 971
Processing row: 972
Assigned RFID 3B0019B8CC to 1 rows in takeoff_match
Processing row: 973
Processing row: 974
Assigned RFID 3B00190DF0 to 1 rows in takeoff_match
Processing row: 975
Processing row: 976
Assigned RFID 01103F97C4 to 1 rows in takeoff_match
Processing row: 977
Assigned RFID 3B00199DE5 to 1 rows in takeoff_match
Processing row: 978
Processing row: 979
Assigned RFID 3B00190DF0 to 0 rows in takeoff_match
Processing row: 980
Processing row: 981
Assigned RFID 3B00190DF0 to 0 rows in takeoff_match
Processing row: 982
Processing row: 983
Assigned RFID 3B00190DF0 to 1 rows in takeoff_match
Processing row: 984
Processing row: 985
Assigned

 16%|█▌        | 2467/15289 [00:00<00:02, 4400.68it/s]

...

Assigned RFID 3B00182DFC to 2 rows in takeoff_match
Processing row: 12129
Processing row: 12130
Assigned RFID 3B0018A99B to 0 rows in takeoff_match
Processing row: 12131
Processing row: 12132
Assigned RFID 3B0018A99B to 1 rows in takeoff_match
Processing row: 12133
Processing row: 12134
Assigned RFID 3B004C4B80 to 0 rows in takeoff_match
Processing row: 12135
Processing row: 12136
Assigned RFID 3B00182A81 to 1 rows in takeoff_match
Processing row: 12137
Processing row: 12138
Assigned RFID 3B0018F763 to 1 rows in takeoff_match
Processing row: 12139
Processing row: 12140
Assigned RFID 3B004C4B80 to 0 rows in takeoff_match
Processing row: 12141
Processing row: 12142
Assigned RFID 011016B2E1 to 0 rows in takeoff_match
Processing row: 12143
Processing row: 12144
Assigned RFID 01103FD532 to 0 rows in takeoff_match
Processing row: 12145
Processing row: 12146
Assigned RFID 0700ED9568 to 0 rows in takeoff_match
Processing row: 12147
Assigned RFID 011016B2E1 to 0 rows in takeoff_match
Processing

 92%|█████████▏| 14097/15289 [00:03<00:00, 4737.40it/s]

Assigned RFID 3B0019B8CC to 0 rows in takeoff_match
Processing row: 13119
Processing row: 13120
Assigned RFID 3B001877B5 to 1 rows in takeoff_match
Processing row: 13121
Processing row: 13122
Assigned RFID 0700ED9568 to 1 rows in takeoff_match
Processing row: 13123
Processing row: 13124
Assigned RFID 3B001857EE to 1 rows in takeoff_match
Processing row: 13125
Processing row: 13126
Assigned RFID 3B0018C2F6 to 1 rows in takeoff_match
Processing row: 13127
Processing row: 13128
Assigned RFID 3B001877B5 to 0 rows in takeoff_match
Processing row: 13129
Assigned RFID 3B0018C2F6 to 0 rows in takeoff_match
Processing row: 13130
Processing row: 13131
Assigned RFID 3B00191394 to 1 rows in takeoff_match
Processing row: 13132
Processing row: 13133
Assigned RFID 01103F97C4 to 0 rows in takeoff_match
Processing row: 13134
Processing row: 13135
Assigned RFID 01103F97C4 to 1 rows in takeoff_match
Processing row: 13136
Processing row: 13137
Assigned RFID 3B004CDB63 to 1 rows in takeoff_match
Processing

100%|██████████| 15289/15289 [00:03<00:00, 4637.17it/s]

Processing row: 14097
Processing row: 14098
Assigned RFID 3B004ACEEA to 1 rows in takeoff_match
Processing row: 14099
Processing row: 14100
Assigned RFID 0700ED9568 to 1 rows in takeoff_match
Processing row: 14101
Processing row: 14102
Assigned RFID 3B004CD4DE to 0 rows in takeoff_match
Processing row: 14103
Processing row: 14104
Assigned RFID 3B0018C2F6 to 1 rows in takeoff_match
Processing row: 14105
Processing row: 14106
Assigned RFID 3B0019F652 to 1 rows in takeoff_match
Processing row: 14107
Processing row: 14108
Assigned RFID 3B004C6A69 to 0 rows in takeoff_match
Processing row: 14109
Processing row: 14110
Assigned RFID 3B0019F652 to 0 rows in takeoff_match
Processing row: 14111
Processing row: 14112
Assigned RFID 0700ED9568 to 2 rows in takeoff_match
Processing row: 14113
Processing row: 14114
Assigned RFID 3B0018C2F6 to 1 rows in takeoff_match
Processing row: 14115
Processing row: 14116
Assigned RFID 3B004C6A69 to 2 rows in takeoff_match
Processing row: 14117
Processing row: 14

In [166]:
# used parallel processing => Filter the takeoff_match DataFrame to exclude rows with pd.NA in the RFID column
print(takeoff_match.head(5))



   takeoff_event                datetime        RFID         day
0              1 2024-12-11 08:00:48.289  3B0018C6F9  2024-12-11
1              2 2024-12-11 08:02:31.780        <NA>  2024-12-11
2              3 2024-12-11 08:02:36.599  3B00185E23  2024-12-11
3              4 2024-12-11 08:03:14.191        <NA>  2024-12-11
4              5 2024-12-11 08:04:49.950        <NA>  2024-12-11


In [167]:

takeoff_filtered2 = takeoff_match[takeoff_match['RFID'].notna()]
print(f"filtered dataset: {takeoff_filtered2.shape}") #2754 #4713 for day-1
print(takeoff_filtered2.head(10))
print(takeoff_filtered2.tail(10))

filtered dataset: (4496, 4)
    takeoff_event                datetime        RFID         day
0               1 2024-12-11 08:00:48.289  3B0018C6F9  2024-12-11
2               3 2024-12-11 08:02:36.599  3B00185E23  2024-12-11
5               6 2024-12-11 08:05:55.755  3B00185CB8  2024-12-11
6               7 2024-12-11 08:05:57.182  3B00185CB8  2024-12-11
7               8 2024-12-11 08:06:16.031  01103FA4B2  2024-12-11
9              10 2024-12-11 08:07:12.539  3B00185CB8  2024-12-11
11             12 2024-12-11 08:07:32.956  3B00190DF0  2024-12-11
17             18 2024-12-11 08:09:27.324  3B00185CB8  2024-12-11
19             20 2024-12-11 08:11:08.505  3B00190DF0  2024-12-11
21             22 2024-12-11 08:11:36.094  01103FA4B2  2024-12-11
       takeoff_event                datetime        RFID         day
11309          11310 2025-02-18 11:27:12.933  3B004AE3AB  2025-02-18
11310          11311 2025-02-18 11:27:21.472  3B004AE3AB  2025-02-18
11311          11312 2025-02-18 11:28:0

In [168]:
takeoff_filtered2['day'] = takeoff_filtered2['datetime'].dt.date
takeoff_filtered2['day'].unique() #yes! now 2025-02-16 in. #02-17 is out for day1 because no IR data for that day. 

array([datetime.date(2024, 12, 11), datetime.date(2024, 12, 14),
       datetime.date(2024, 12, 22), datetime.date(2024, 12, 30),
       datetime.date(2025, 1, 2), datetime.date(2025, 1, 20),
       datetime.date(2025, 1, 23), datetime.date(2025, 1, 29),
       datetime.date(2025, 2, 5), datetime.date(2025, 2, 11),
       datetime.date(2025, 2, 15), datetime.date(2025, 2, 18)],
      dtype=object)

In [169]:
#save it!!!
takeoff_filtered2.to_csv('IRFID_matched_day-1.csv')
#amazing! These are the birds with all 5 sensor reads at takeoff, with the first sensor reading between arrive and depart. 
#question could be made if it's possible that a bird has its RFID read without triggering sensor1. 
#I could also additionally filter those where RFID is read first, then sensor1, then depart. ===> this is basically what I filtered.
#It is justifiable as if the bird trigeered the sensor1 and it is
# For the cases where it could be sensor1, arrivalRFID, sensor1, departRFID, I could try filling takeoff_event dataframe as the mean of sensor1 reading. 
# 1. see how short usually is the time between first and last reading of sensor1 per takeoff_event. 
# 2. if it's short enough, try the mean of sensor1 and see if it filters out more matches. 
# 3. in fact, doesn't matter as sensor1 had a limit to be logged by less than 0.5 second. 
# and if the sensor1 was before being on the perch, it would be more than 1 second.
#  

### matching to the full IR dataset.

In [170]:
irfid = pd.read_csv('IRFID_matched_day-1.csv', index_col = 0, dtype = {'Sensor':str, 'RFID':str})
# Convert 'datetime' column to datetime type for easier manipulation and filtering
irfid['datetime'] = pd.to_datetime(irfid['datetime'], format='%Y-%m-%d %H:%M:%S.%f')

print(f"irfid_matched shape: {irfid.shape}")
print(irfid.head(5))
print(irfid.dtypes)
print(type(irfid))
print(irfid['day'].unique())

irfid_matched shape: (4496, 4)
   takeoff_event                datetime        RFID         day
0              1 2024-12-11 08:00:48.289  3B0018C6F9  2024-12-11
2              3 2024-12-11 08:02:36.599  3B00185E23  2024-12-11
5              6 2024-12-11 08:05:55.755  3B00185CB8  2024-12-11
6              7 2024-12-11 08:05:57.182  3B00185CB8  2024-12-11
7              8 2024-12-11 08:06:16.031  01103FA4B2  2024-12-11
takeoff_event             int64
datetime         datetime64[ns]
RFID                     object
day                      object
dtype: object
<class 'pandas.core.frame.DataFrame'>
['2024-12-11' '2024-12-14' '2024-12-22' '2024-12-30' '2025-01-02'
 '2025-01-20' '2025-01-23' '2025-01-29' '2025-02-05' '2025-02-11'
 '2025-02-15' '2025-02-18']


In [171]:
print(final_filtered_df.dtypes)
#choose just 'takeoff_event' and 'RFID' columns and 
#match filterd_df and irfid data types by column 'takeoff_event'
final_match_key = irfid[["takeoff_event","RFID"]] 
irfid_final =pd.merge(final_filtered_df,final_match_key, on='takeoff_event')


level_0                   int64
index                     int64
Sensor                   object
Time                    float64
datetime         datetime64[ns]
takeoff_event             int64
day                      object
dtype: object


In [172]:
print(irfid_final.head(5))
print(irfid_final.tail(5)) #looking great! 
print(irfid_final.shape) #20158 -> 23613 after adding 02-16
#18506 for day1 


   level_0  index Sensor          Time                datetime  takeoff_event  \
0        0    134      1  1.733904e+12 2024-12-11 08:00:48.289              1   
1        1    136      1  1.733904e+12 2024-12-11 08:00:48.352              1   
2        2    137      1  1.733904e+12 2024-12-11 08:00:48.356              1   
3        3    138      1  1.733904e+12 2024-12-11 08:00:48.419              1   
4        4    140      2  1.733904e+12 2024-12-11 08:00:48.572              1   

          day        RFID  
0  2024-12-11  3B0018C6F9  
1  2024-12-11  3B0018C6F9  
2  2024-12-11  3B0018C6F9  
3  2024-12-11  3B0018C6F9  
4  2024-12-11  3B0018C6F9  
       level_0   index Sensor          Time                datetime  \
31326   108785  248649      1  1.739878e+12 2025-02-18 11:29:56.038   
31327   108786  248650      2  1.739878e+12 2025-02-18 11:29:56.112   
31328   108787  248651      3  1.739878e+12 2025-02-18 11:29:56.185   
31329   108788  248652      4  1.739878e+12 2025-02-18 11:29:

#### save it!

In [173]:
irfid_final.to_csv('irfid_final_day-1.csv', index = 0) #previous code with all dates

In [174]:
irfid_final['Sensor'] = irfid_final['Sensor'].astype(int)
irfid_final.dtypes

level_0                   int64
index                     int64
Sensor                    int32
Time                    float64
datetime         datetime64[ns]
takeoff_event             int64
day                      object
RFID                     object
dtype: object

In [175]:
len(irfid_final) #20158 -> 23613
#day1 = 18506

31331

In [176]:
irfid_final.shape

(31331, 8)

## finding firstbroken & lastbroken 

In [177]:
# Initialize the results list
results_list = []

# make sure correct dataset is fed
df = irfid_final

# Initialize start_index
start_index = 0

# Iterate over the DataFrame
for i in range(len(df)):
    first_read = df['Time'].iloc[start_index]
    current_sensor = df['Sensor'].iloc[start_index]

    #rfid assignment
    rfid = df['RFID'].iloc[start_index] if current_sensor == 1 else pd.NA

    # Debugging print statements 
    print(f"Iteration {i}:")
    print(f"  start_index: {start_index}")
    print(f"  first_read: {first_read}")
    print(f"  current_sensor: {current_sensor}")
    print(f"  rfid: {rfid}")


    for j in range(start_index, len(irfid_final)):
        if df['Sensor'].iloc[j] != current_sensor:
            start_index = j
            print(f"  Sensor changed at index {j}, new start_index: {start_index}")
            break

    results_list.append({
        f'RFID': rfid,
        f'firstbroken{current_sensor}': first_read,
    })

# Convert results_list to DataFrame
results_df = pd.DataFrame(results_list)

print(results_df)

Iteration 0:
  start_index: 0
  first_read: 1733904048289.0
  current_sensor: 1
  rfid: 3B0018C6F9
  Sensor changed at index 4, new start_index: 4
Iteration 1:
  start_index: 4
  first_read: 1733904048572.0
  current_sensor: 2
  rfid: <NA>
  Sensor changed at index 7, new start_index: 7
Iteration 2:
  start_index: 7
  first_read: 1733904048703.0
  current_sensor: 3
  rfid: <NA>
  Sensor changed at index 9, new start_index: 9
Iteration 3:
  start_index: 9
  first_read: 1733904048761.0
  current_sensor: 4
  rfid: <NA>
  Sensor changed at index 11, new start_index: 11
Iteration 4:
  start_index: 11
  first_read: 1733904048828.0
  current_sensor: 5
  rfid: <NA>
  Sensor changed at index 13, new start_index: 13
Iteration 5:
  start_index: 13
  first_read: 1733904156599.0
  current_sensor: 1
  rfid: 3B00185E23
  Sensor changed at index 17, new start_index: 17
Iteration 6:
  start_index: 17
  first_read: 1733904156733.0
  current_sensor: 2
  rfid: <NA>
  Sensor changed at index 19, new start_

In [178]:
results_df.head(10)

RFID  firstbroken1  firstbroken2  firstbroken3  firstbroken4  \
0  3B0018C6F9  1.733904e+12           NaN           NaN           NaN   
1        <NA>           NaN  1.733904e+12           NaN           NaN   
2        <NA>           NaN           NaN  1.733904e+12           NaN   
3        <NA>           NaN           NaN           NaN  1.733904e+12   
4        <NA>           NaN           NaN           NaN           NaN   
5  3B00185E23  1.733904e+12           NaN           NaN           NaN   
6        <NA>           NaN  1.733904e+12           NaN           NaN   
7        <NA>           NaN           NaN  1.733904e+12           NaN   
8        <NA>           NaN           NaN           NaN  1.733904e+12   
9        <NA>           NaN           NaN           NaN           NaN   

   firstbroken5  
0           NaN  
1           NaN  
2           NaN  
3           NaN  
4  1.733904e+12  
5           NaN  
6           NaN  
7           NaN  
8           NaN  
9  1.733904e+12

In [179]:
import pandas as pd

# Initialize an empty DataFrame with specified columns
irfid_alligned = pd.DataFrame(columns=['RFID', 'firstbroken1', 'firstbroken2', 'firstbroken3', 'firstbroken4', 'firstbroken5'])

# Iterate through results_df
for i in range(len(results_df) - 4):
    if pd.notna(results_df['RFID'].iloc[i]):
        rfid = results_df['RFID'].iloc[i]
        firstbroken1 = results_df['firstbroken1'].iloc[i]
        firstbroken2 = results_df['firstbroken2'].iloc[i+1]
        firstbroken3 = results_df['firstbroken3'].iloc[i+2]
        firstbroken4 = results_df['firstbroken4'].iloc[i+3]
        firstbroken5 = results_df['firstbroken5'].iloc[i+4]
        firstbroken_values = [firstbroken1, firstbroken2, firstbroken3, firstbroken4, firstbroken5]

        #print(f"Checking row {i}: RFID={rfid}, firstbroken_values={firstbroken_values}")

        if pd.notna(firstbroken_values).all():
            row = [rfid] + firstbroken_values
            irfid_alligned.loc[len(irfid_alligned)] = row

print(irfid_alligned) #3041 -> 3055 #2754

            RFID  firstbroken1  firstbroken2  firstbroken3  firstbroken4  \
0     3B0018C6F9  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
1     3B00185E23  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
2     3B00185CB8  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
3     3B00185CB8  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
4     01103FA4B2  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
...          ...           ...           ...           ...           ...   
4489  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   
4490  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   
4491  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   
4492  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   
4493  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   

      firstbroken5  
0     1.733904e+12  
1     1.733904e+12  
2     1.733904e+12  
3  

In [180]:
irfid_alligned.to_csv('irfid_alligned_day-1.csv') 
#last run 2025-05-08

## matching Time

In [181]:
print(irfid_final.head(5))
print(irfid_final.dtypes)
print(irfid_final.shape)
print(irfid_final['day'].unique())

   level_0  index  Sensor          Time                datetime  \
0        0    134       1  1.733904e+12 2024-12-11 08:00:48.289   
1        1    136       1  1.733904e+12 2024-12-11 08:00:48.352   
2        2    137       1  1.733904e+12 2024-12-11 08:00:48.356   
3        3    138       1  1.733904e+12 2024-12-11 08:00:48.419   
4        4    140       2  1.733904e+12 2024-12-11 08:00:48.572   

   takeoff_event         day        RFID  
0              1  2024-12-11  3B0018C6F9  
1              1  2024-12-11  3B0018C6F9  
2              1  2024-12-11  3B0018C6F9  
3              1  2024-12-11  3B0018C6F9  
4              1  2024-12-11  3B0018C6F9  
level_0                   int64
index                     int64
Sensor                    int32
Time                    float64
datetime         datetime64[ns]
takeoff_event             int64
day                      object
RFID                     object
dtype: object
(31331, 8)
[datetime.date(2024, 12, 11) datetime.date(2024, 12, 14)
 

In [182]:
irfid_final_timematch = irfid_final[irfid_final['Sensor']==1]
irfid_final_timematch = irfid_final_timematch.rename(columns={'Time':'firstbroken1'})
irfid_final_timematch = irfid_final_timematch.drop(['Sensor'], axis = 1)
irfid_final_timematch = irfid_final_timematch.reset_index(drop = True)
print(irfid_final_timematch.shape)
print(irfid_final_timematch.head(3))

(10154, 7)
   level_0  index  firstbroken1                datetime  takeoff_event  \
0        0    134  1.733904e+12 2024-12-11 08:00:48.289              1   
1        1    136  1.733904e+12 2024-12-11 08:00:48.352              1   
2        2    137  1.733904e+12 2024-12-11 08:00:48.356              1   

          day        RFID  
0  2024-12-11  3B0018C6F9  
1  2024-12-11  3B0018C6F9  
2  2024-12-11  3B0018C6F9  


In [183]:
irfid_alligned.head(3)

RFID  firstbroken1  firstbroken2  firstbroken3  firstbroken4  \
0  3B0018C6F9  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
1  3B00185E23  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
2  3B00185CB8  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   

   firstbroken5  
0  1.733904e+12  
1  1.733904e+12  
2  1.733904e+12

In [184]:
irfid_new = pd.merge(irfid_alligned, irfid_final_timematch,  on = ['firstbroken1','RFID'])

In [185]:
irfid_new = irfid_new.drop(['index'], axis = 1)
irfid_new

RFID  firstbroken1  firstbroken2  firstbroken3  firstbroken4  \
0     3B0018C6F9  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
1     3B00185E23  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
2     3B00185CB8  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
3     3B00185CB8  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
4     01103FA4B2  1.733904e+12  1.733904e+12  1.733904e+12  1.733904e+12   
...          ...           ...           ...           ...           ...   
4489  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   
4490  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   
4491  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   
4492  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   
4493  3B004AE3AB  1.739878e+12  1.739878e+12  1.739878e+12  1.739878e+12   

      firstbroken5  level_0                datetime  takeoff_event         day  
0     1.733904e+12        0 2024-12-11 08:00:48.289              1  2024-12-11  
1     1.733904e+12       37 2024-12-11 08:02:36.599              3  2024-12-11  
2     1.733904e+12       86 2024-12-11 08:05:55.755              6  2024-12-11  
3     1.733904e+12      101 2024-12-11 08:05:57.182              7  2024-12-11  
4     1.733904e+12      127 2024-12-11 08:06:16.031              8  2024-12-11  
...            ...      ...                     ...            ...         ...  
4489  1.739878e+12   108752 2025-02-18 11:28:37.188          11315  2025-02-18  
4490  1.739878e+12   108758 2025-02-18 11:29:08.157          11316  2025-02-18  
4491  1.739878e+12   108768 2025-02-18 11:29:25.089          11317  2025-02-18  
4492  1.739878e+12   108776 2025-02-18 11:29:48.565          11318  2025-02-18  
4493  1.739878e+12   108784 2025-02-18 11:29:55.964          11319  2025-02-18  

[4494 rows x 10 columns]

In [186]:
irfid_calc = pd.DataFrame()
irfid_calc = irfid_new
#seconds
irfid_calc['firstbroken1'] = irfid_calc['firstbroken1']/1000
irfid_calc['firstbroken2'] = irfid_calc['firstbroken2']/1000
irfid_calc['firstbroken3'] = irfid_calc['firstbroken3']/1000
irfid_calc['firstbroken4'] = irfid_calc['firstbroken4']/1000
irfid_calc['firstbroken5'] = irfid_calc['firstbroken5']/1000

#time
irfid_calc['t12'] = irfid_calc['firstbroken2'] - irfid_calc['firstbroken1']
irfid_calc['t23'] = irfid_calc['firstbroken3'] - irfid_calc['firstbroken2']
irfid_calc['t34'] = irfid_calc['firstbroken4'] - irfid_calc['firstbroken3']
irfid_calc['t45'] = irfid_calc['firstbroken5'] - irfid_calc['firstbroken4']

#speed
irfid_calc['v1'] = 0.135/irfid_calc['t12']
irfid_calc['v2'] = 0.135/irfid_calc['t23']
irfid_calc['v3'] = 0.135/irfid_calc['t34']
irfid_calc['v4'] = 0.135/irfid_calc['t45']
irfid_calc['avg.v'] = 0.540/(irfid_calc['firstbroken5'] - irfid_calc['firstbroken1'])

#acceleration
irfid_calc['acc1'] = 2*(irfid_calc['v2'] - irfid_calc['v1'])/(irfid_calc['t12'] + irfid_calc['t23'])
irfid_calc['acc2'] = 2*(irfid_calc['v3'] - irfid_calc['v2'])/(irfid_calc['t23'] + irfid_calc['t34'])
irfid_calc['acc3'] = 2*(irfid_calc['v4'] - irfid_calc['v3'])/(irfid_calc['t34'] + irfid_calc['t45'])
irfid_calc['avg.acc'] = irfid_calc['v4'] - irfid_calc['v1']/(irfid_calc['t23']+irfid_calc['t34']+1/2*(irfid_calc['t12']+irfid_calc['t45']))

#filtering
irfid_calc[(irfid_calc['t12'] <0.25 )& (irfid_calc['t23'] <0.25)] #flying bird should exit the section less than quarter of a second.
print(irfid_calc.head(3))
print(irfid_calc.shape)

         RFID  firstbroken1  firstbroken2  firstbroken3  firstbroken4  \
0  3B0018C6F9  1.733904e+09  1.733904e+09  1.733904e+09  1.733904e+09   
1  3B00185E23  1.733904e+09  1.733904e+09  1.733904e+09  1.733904e+09   
2  3B00185CB8  1.733904e+09  1.733904e+09  1.733904e+09  1.733904e+09   

   firstbroken5  level_0                datetime  takeoff_event         day  \
0  1.733904e+09        0 2024-12-11 08:00:48.289              1  2024-12-11   
1  1.733904e+09       37 2024-12-11 08:02:36.599              3  2024-12-11   
2  1.733904e+09       86 2024-12-11 08:05:55.755              6  2024-12-11   

   ...    t45        v1        v2        v3        v4     avg.v       acc1  \
0  ...  0.067  0.477032  1.030534  2.327592  2.014921  1.001855   2.673923   
1  ...  0.074  1.007462  1.956522  2.288135  1.824327  1.607143   9.350335   
2  ...  0.065  0.937501  2.142858  1.874999  2.076921  1.569768  11.645975   

        acc2      acc3   avg.acc  
0  13.725492 -5.002743  0.704394  
1   5.1

## Saved! 

In [187]:
irfid_calc.to_csv('irfid_calc_day-1.csv') #uploaded 2025-05-08

# E. RFID - Force marry

## a. data prepping and define the date to process

## b. INSERT DATE

### dummy 

In [1]:
import pandas as pd
import glob
import re

# Define the folder containing the files
folder_path = "C:\\Users\\kmh\\Documents\\DATA\\dummy_data"

# Get all .txt files in the folder
file_list = glob.glob(f"{folder_path}\\*.txt")

# Initialize an empty list to store dataframes
dataframes = []

for file in file_list:
    # Extract relevant information from the filename using regex
    match = re.search(r"day(-?\d+)_(\w+)_(\d+)", file.split("\\")[-1])  
    
    if match:
        day_since = match.group(1)  # Extract day as a character
        flight_type = match.group(2)  # Extract flight type
        event = int(match.group(3))  # Extract event
        
        scare_outcome = "1" if flight_type == "escape" else "0"  # Convert scare outcome to character
        
        # Read the data from the file with comma as separator
        df = pd.read_csv(file, header=None, sep=",")
        
        # Set column names
        df.columns = ["V1", "V2", "V3", "V4", "V5", "V6", "t"]
        
        # Add extracted values as new columns with correct types
        df["day_since"] = day_since  # Keep as character
        df["scare_outcome"] = scare_outcome  # Keep as character
        df["event"] = event  # Keep as character
        
        # Append dataframe to the list
        dataframes.append(df)

# Concatenate all dataframes into one
raw_df = pd.concat(dataframes, ignore_index=True)

# Display first few rows
print(raw_df.head())

# Save to a new CSV file if needed
#final_df.to_csv("F:\\FTdata\\2025_dummy\\concatenated_data.csv", index=False)


      V1     V2     V3     V4     V5     V6             t day_since  \
0  0.799 -0.099 -0.737 -0.054 -0.022  0.093  3.832497e+09        -1   
1  0.799 -0.099 -0.738 -0.055 -0.020  0.094  3.832497e+09        -1   
2  0.800 -0.099 -0.741 -0.054 -0.020  0.094  3.832497e+09        -1   
3  0.801 -0.100 -0.742 -0.053 -0.016  0.096  3.832497e+09        -1   
4  0.803 -0.099 -0.745 -0.054 -0.017  0.095  3.832497e+09        -1   

  scare_outcome  event  
0             0      1  
1             0      1  
2             0      1  
3             0      1  
4             0      1  


In [2]:
raw_df["event3"] = "day" + raw_df["day_since"].astype(str) + "_" + raw_df["scare_outcome"] + "_" + raw_df["event"].astype(str)



In [3]:
raw_df.head()

V1     V2     V3     V4     V5     V6             t day_since  \
0  0.799 -0.099 -0.737 -0.054 -0.022  0.093  3.832497e+09        -1   
1  0.799 -0.099 -0.738 -0.055 -0.020  0.094  3.832497e+09        -1   
2  0.800 -0.099 -0.741 -0.054 -0.020  0.094  3.832497e+09        -1   
3  0.801 -0.100 -0.742 -0.053 -0.016  0.096  3.832497e+09        -1   
4  0.803 -0.099 -0.745 -0.054 -0.017  0.095  3.832497e+09        -1   

  scare_outcome  event     event3  
0             0      1  day-1_0_1  
1             0      1  day-1_0_1  
2             0      1  day-1_0_1  
3             0      1  day-1_0_1  
4             0      1  day-1_0_1

In [4]:
raw_df['event3'].nunique()

60

In [5]:
raw_df.to_csv('raw_df.csv')

In [46]:
# Load the manual calibration matrix
manual_calibration_matrix = pd.read_csv('../data/manual_calibration_matrix.csv', header=None)
manual_calibration_matrix.columns = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6']

In [47]:
voltage_df1 = raw_df[['V1','V2','V3','V4','V5','V6']]
#drop the rows with NaN

# Transform voltage file
F_calc = np.dot(voltage_df1, manual_calibration_matrix)
F_df = pd.DataFrame(F_calc, columns=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz'])

combined_df = pd.concat([F_df, raw_df[['t','day_since', 'scare_outcome', 'event', 'event3']]], axis=1)

combined_df.head()

Fx        Fy        Fz        Tx        Ty        Tz             t  \
0  0.182042  0.092480  0.014225 -0.007937  0.012437  0.000639  3.832497e+09   
1  0.184155  0.092476  0.015027 -0.007973  0.012423  0.000639  3.832497e+09   
2  0.183424  0.092965  0.013449 -0.008004  0.012465  0.000630  3.832497e+09   
3  0.184636  0.096099  0.016455 -0.008043  0.012467  0.000611  3.832497e+09   
4  0.184609  0.093351  0.014899 -0.008084  0.012496  0.000621  3.832497e+09   

  day_since scare_outcome  event     event3  
0        -1             0      1  day-1_0_1  
1        -1             0      1  day-1_0_1  
2        -1             0      1  day-1_0_1  
3        -1             0      1  day-1_0_1  
4        -1             0      1  day-1_0_1

In [48]:
combined_df.to_csv('../data/dummy_F.csv' )

In [49]:
combined_df['datetime'] = combined_df['t'].apply(force_defs.convert_time_force)
combined_df['RFID'] = pd.NA
#combined_df['event'] = pd.NA
combined_df['datetime'] = pd.to_datetime(combined_df['datetime'], format='%Y-%m-%d %H:%M:%S:%f')

In [50]:
combined_df.head(5)

Fx        Fy        Fz        Tx        Ty        Tz             t  \
0  0.182042  0.092480  0.014225 -0.007937  0.012437  0.000639  3.832497e+09   
1  0.184155  0.092476  0.015027 -0.007973  0.012423  0.000639  3.832497e+09   
2  0.183424  0.092965  0.013449 -0.008004  0.012465  0.000630  3.832497e+09   
3  0.184636  0.096099  0.016455 -0.008043  0.012467  0.000611  3.832497e+09   
4  0.184609  0.093351  0.014899 -0.008084  0.012496  0.000621  3.832497e+09   

  day_since scare_outcome  event     event3                datetime  RFID  
0        -1             0      1  day-1_0_1 2025-06-11 14:32:54.260  <NA>  
1        -1             0      1  day-1_0_1 2025-06-11 14:32:54.260  <NA>  
2        -1             0      1  day-1_0_1 2025-06-11 14:32:54.260  <NA>  
3        -1             0      1  day-1_0_1 2025-06-11 14:32:54.260  <NA>  
4        -1             0      1  day-1_0_1 2025-06-11 14:32:54.260  <NA>

In [51]:
combined_df.to_csv('../data/dummy_F2.csv' )

In [ ]:
#no rfid file - it's all me! 
# concatenate 60 files in F:\FTdata\2025_dummy
# file names in day{day}_{flight_type}{event}
# concatenate into columns "V1","V2","V3","V4","V5","V6", "t", 
# make "day_since" column with the values at {day} from their source file name
# make "scare_outcome" column, of which value is 1 if {flight_type} in the source file name was "escape", and 0 if it was "normal"
#make "event" column, of which value is {event} in the source file. 
#for example, if the file name is "day0_escape5", the "day_since" value will be "0", "scare_outcome" 1, and "event", 5
# "datetime", "RFID", and "event"
# "datetime" is 
# concatenate all the files in '2025_dummy' file with columns "Fx", "Fy","Fz","Tx","Ty","Tz","t","datetime","RFID",and "event"

### F as timestamp 

In [ ]:
import os
import glob
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from tqdm import tqdm
import warnings

warnings.filterwarnings('ignore')

# CHANGE HERE
rfid_file = r'C:\Users\kmh\Documents\DATA\2024-5\RFID\RFID\2024-12-12_RFID_RFID.csv' #this is the date I am dealing with now. 

# Extract the date from the RFID file name
base_name = os.path.basename(rfid_file)
date_part = base_name.split('_')[0]


# Load the manual calibration matrix
manual_calibration_matrix = pd.read_csv('manual_calibration_matrix.csv', header=None)
manual_calibration_matrix.columns = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6']

# Define the paths
force_path = r'C:\Users\kmh\Documents\DATA\2024-5\FT\F'
voltage_path = r'C:\Users\kmh\Documents\DATA\2024-5\FT\V'

# Initialize final DataFrames to store results
final_F_matched = pd.DataFrame()
final_F_match_keys = pd.DataFrame()


# Convert date format from yyyy-mm-dd to yyyy_mm_dd
date_part_formatted = date_part.replace('-', '_')
print(f'date_part_formatted: {date_part_formatted}')

# Construct the corresponding force and voltage file names
force_file = os.path.join(force_path, f'F_{date_part_formatted}.txt')
voltage_file = os.path.join(voltage_path, f'V_{date_part_formatted}.txt')
    
# Load dataframes
rfid_df = pd.read_csv(rfid_file, dtype={'epoch_time': float})
force_df = pd.read_csv(force_file, names=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz', 't'], header=None)
voltage_df = pd.read_csv(voltage_file, names=['V1', 'V2', 'V3', 'V4', 'V5', 'V6'], header=None)
    
# Transform voltage file
F_calc = np.dot(voltage_df, manual_calibration_matrix)
F_df = pd.DataFrame(F_calc, columns=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz'])
F_df['t'] = force_df['t']

#drop the rows with NaN
F_df = F_df.dropna()

# Apply the function to the 'Time' column
F_df['datetime'] = F_df['t'].apply(force_defs.convert_time_force)
F_df['RFID'] = pd.NA
F_df['event'] = pd.NA
F_df['datetime'] = pd.to_datetime(F_df['datetime'], format='%Y-%m-%d %H:%M:%S:%f')

#print(F_df.dtypes)

# Trim down RFID file
RFID_match = rfid_df[['id', 'status', 'epoch_time']]
RFID_match.loc[:, 'id'] = RFID_match['id'].astype(str)  # Ensure 'id' is treated as string
RFID_match.loc[:, 'rfid_datetime'] = RFID_match['epoch_time'].apply(defs.convert_time_rfid) #changed 'epoch_time_converted' -> 'rfid_datetime'
RFID_match['rfid_datetime'] = pd.to_datetime(RFID_match['rfid_datetime'], format='%Y-%m-%d %H:%M:%S:%f')
RFID_match = RFID_match[(RFID_match['id'].str.len() == 10) & (~RFID_match['id'].str.contains('?', regex=False))]
RFID_match.reset_index(drop=True, inplace=True)  # Reset the index
#print(f'RFID_match.head(5): {RFID_match.head(5)}')

F_match_keys, RFID_match_keys = defs.match_keys_preparation(F_df, RFID_match)
#print(f'RFID_match_keys.dtypes: {RFID_match_keys.dtypes}')
print(f'RFID_match_keys: {RFID_match_keys.head(5)}')
#print(F_match_keys.dtypes)
print(f'F_match_keys:{F_match_keys.head(5)}' )

# Initialize a list to store current_F_valid for each iteration
all_F_thisfile = []
all_F_matchkeys_thisloop = []
start_index = 0

#reset RFID_match_keys' index to prevent KeyError
RFID_match_keys.reset_index(drop=True, inplace=True)


date_part_formatted: 2024_12_12
RFID_match_keys:    hr  min   s        rfid  status timestamp
0   7   53  20  3B00185CB8  Arrive  07:53:20
1   7   53  20  3B00185CB8  Depart  07:53:20
2   7   53  20  3B00485E69  Arrive  07:53:20
3   7   53  20  3B00485E69  Depart  07:53:20
4   7   53  20  3B0018A99B  Arrive  07:53:20
F_match_keys:   index  hr  min   s timestamp  event  RFID
0      0   8    5  19  08:05:19      1  <NA>
1   1000   8    5  20  08:05:20      1  <NA>
2   2000   8    5  43  08:05:43      2  <NA>
3   3000   8    6  33  08:06:33      3  <NA>
4   4000   8    6  37  08:06:37      4  <NA>


In [13]:
RFID_match_keys

hr  min   s        rfid  status timestamp
0     7   53  20  3B00185CB8  Arrive  07:53:20
1     7   53  20  3B00185CB8  Depart  07:53:20
2     7   53  20  3B00485E69  Arrive  07:53:20
3     7   53  20  3B00485E69  Depart  07:53:20
4     7   53  20  3B0018A99B  Arrive  07:53:20
..   ..  ...  ..         ...     ...       ...
158  16   13  20  3B0019B8CC  Depart  16:13:20
159  16   13  20  01103F97C4  Arrive  16:13:20
160  16   13  20  01103F97C4  Depart  16:13:20
161  16   13  20  3B001877B5  Arrive  16:13:20
162  16   13  20  3B001877B5  Depart  16:13:20

[163 rows x 6 columns]

In [14]:
F_match_keys

index  hr  min   s timestamp  event  RFID
0           0   8    5  19  08:05:19      1  <NA>
1        1000   8    5  20  08:05:20      1  <NA>
2        2000   8    5  43  08:05:43      2  <NA>
3        3000   8    6  33  08:06:33      3  <NA>
4        4000   8    6  37  08:06:37      4  <NA>
...       ...  ..  ...  ..       ...    ...   ...
1682  1682000  15   43  18  15:43:18    710  <NA>
1683  1683000  15   43  19  15:43:19    710  <NA>
1684  1684000  15   43  32  15:43:32    711  <NA>
1685  1685000  15   43  33  15:43:33    711  <NA>
1686  1686000  15   43  34  15:43:34    711  <NA>

[1687 rows x 7 columns]

### F as timestamp (no V) 
- 2025-01-22 data

In [8]:
ati_matrix =pd.read_csv('ati_calibration_matrix.csv', header = None)
ati_matrix.columns = ['Fx','Fy','Fz','Tx','Ty','Tz']
ati_matrix


Fx        Fy         Fz        Tx         Ty        Tz
0   0.004811  0.006008   0.053250  1.137180  -0.030701 -1.128740
1  -0.043528 -1.302720   0.031501  0.658127   0.010534  0.655168
2   0.751754 -0.008501   0.775567 -0.013982   0.769775 -0.006158
3  -0.008589 -5.668460  11.482100  2.741270 -11.039900  2.838030
4 -12.684700  0.240579   6.307570 -5.067440   6.553150  4.893120
5  -0.350987 -9.465280  -0.449229 -9.724680  -0.229432 -9.376970

In [71]:
import os
import glob
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from tqdm import tqdm
import warnings

warnings.filterwarnings('ignore')

# CHANGE HERE
rfid_file = r'C:\Users\kmh\Documents\DATA\2024-5\RFID\RFID\2024-12-12_RFID_RFID.csv' #this is the date I am dealing with now. 

# Extract the date from the RFID file name
base_name = os.path.basename(rfid_file)
date_part = base_name.split('_')[0]


# Load the manual calibration matrix
manual_calibration_matrix = pd.read_csv('manual_calibration_matrix.csv', header=None)
manual_calibration_matrix.columns = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6']

# Define the paths
force_path = r'C:\Users\kmh\Documents\DATA\2024-5\FT\F'
#voltage_path = r'C:\Users\kmh\Documents\DATA\2024-5\FT\V'

# Initialize final DataFrames to store results
final_F_matched = pd.DataFrame()
final_F_match_keys = pd.DataFrame()


# Convert date format from yyyy-mm-dd to yyyy_mm_dd
date_part_formatted = date_part.replace('-', '_')
print(f'date_part_formatted: {date_part_formatted}')

# Construct the corresponding force and voltage file names
force_file = os.path.join(force_path, f'F_{date_part_formatted}.txt')
#voltage_file = os.path.join(voltage_path, f'V_{date_part_formatted}.txt')
    
# Load dataframes
rfid_df = pd.read_csv(rfid_file, dtype={'epoch_time': float})
force_df = pd.read_csv(force_file, names=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz', 't'], header=None)
#voltage_df = pd.read_csv(voltage_file, names=['V1', 'V2', 'V3', 'V4', 'V5', 'V6'], header=None)
    
#save the time 

# Create an empty DataFrame with column 't'
force_t = pd.DataFrame(columns=['t'])

# Save 't' column values from force_df into force_t
force_t['t'] = force_df['t'].copy()


force_df = force_df.drop(columns=['t'])

# Transform voltage file
#inverse matrix of ati manual calibration
ati_inv = np.linalg.inv(ati_matrix)
#get voltage file 
voltage_df = np.dot(force_df, ati_inv)
voltage_df = pd.DataFrame(voltage_df, columns=['V1', 'V2', 'V3', 'V4', 'V5', 'V6'])
print(f"voltage_df head:{voltage_df.head(3)}")

F_calc = np.dot(voltage_df, manual_calibration_matrix)
F_df = pd.DataFrame(F_calc, columns=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz'])
F_df['t'] = force_t['t']

#drop the rows with NaN
F_df = F_df.dropna()

# Apply the function to the 'Time' column
F_df['datetime'] = F_df['t'].apply(defs.convert_time_force)
F_df['RFID'] = pd.NA
F_df['event'] = pd.NA
F_df['datetime'] = pd.to_datetime(F_df['datetime'], format='%Y-%m-%d %H:%M:%S:%f')

#print(F_df.dtypes)

# Trim down RFID file
RFID_match = rfid_df[['id', 'status', 'epoch_time']]
RFID_match.loc[:, 'id'] = RFID_match['id'].astype(str)  # Ensure 'id' is treated as string
RFID_match.loc[:, 'epoch_time_converted'] = RFID_match['epoch_time'].apply(defs.convert_time_rfid)
RFID_match['epoch_time_converted'] = pd.to_datetime(RFID_match['epoch_time_converted'], format='%Y-%m-%d %H:%M:%S:%f')
RFID_match = RFID_match[(RFID_match['id'].str.len() == 10) & (~RFID_match['id'].str.contains('?', regex=False))]
RFID_match.reset_index(drop=True, inplace=True)  # Reset the index
#print(f'RFID_match.head(5): {RFID_match.head(5)}')

F_match_keys, RFID_match_keys = defs.match_keys_preparation(F_df, RFID_match)
#print(f'RFID_match_keys.dtypes: {RFID_match_keys.dtypes}')
print(f'RFID_match_keys: {RFID_match_keys.head(5)}')
#print(F_match_keys.dtypes)
print(f'F_match_keys:{F_match_keys.head(5)}' )

# Initialize a list to store current_F_valid for each iteration
all_F_thisfile = []
all_F_matchkeys_thisloop = []
start_index = 0

#reset RFID_match_keys' index to prevent KeyError
RFID_match_keys.reset_index(drop=True, inplace=True)


date_part_formatted: 2024_12_12
voltage_df head:         V1        V2        V3        V4        V5        V6
0  0.602080 -0.051396 -0.450999 -0.008232 -0.077219  0.024668
1  0.579802 -0.060855 -0.467957 -0.020700 -0.114736  0.034809
2  1.438125 -0.041145 -0.429274 -0.124889 -1.019486  0.091022
RFID_match_keys:    hr  min   s        rfid  status timestamp
0   7   53  20  3B00185CB8  Arrive  07:53:20
1   7   53  20  3B00185CB8  Depart  07:53:20
2   7   53  20  3B00485E69  Arrive  07:53:20
3   7   53  20  3B00485E69  Depart  07:53:20
4   7   53  20  3B0018A99B  Arrive  07:53:20
F_match_keys:   index  hr  min   s timestamp  event  RFID
0      0   8    5  19  08:05:19      1  <NA>
1   1000   8    5  20  08:05:20      1  <NA>
2   2000   8    5  43  08:05:43      2  <NA>
3   3000   8    6  33  08:06:33      3  <NA>
4   4000   8    6  37  08:06:37      4  <NA>


In [8]:
F_match_keys

index  hr  min   s timestamp  event  RFID
0           0   7   51  39  07:51:39      1  <NA>
1        1000   7   51  40  07:51:40      1  <NA>
2        2000   7   54  47  07:54:47      2  <NA>
3        3000   7   54  48  07:54:48      2  <NA>
4        4000   7   54  49  07:54:49      2  <NA>
...       ...  ..  ...  ..       ...    ...   ...
1779  1779000  16   13  42  16:13:42    752  <NA>
1780  1780000  16   13  55  16:13:55    753  <NA>
1781  1781000  16   13  56  16:13:56    753  <NA>
1782  1782000  16   14   2  16:14:02    754  <NA>
1783  1783000  16   14   5  16:14:05    755  <NA>

[1784 rows x 7 columns]

### F as timestamp using 'time' for RFID

In [ ]:
#used for re-construction 2024-12-12 matchkets
import os
import glob
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from tqdm import tqdm
import warnings

warnings.filterwarnings('ignore')

# CHANGE HERE
rfid_file = r'C:\Users\kmh\Documents\DATA\2024-5\RFID\RFID\2024-12-12_RFID_RFID.csv' #this is the date I am dealing with now. 

# Extract the date from the RFID file name
base_name = os.path.basename(rfid_file)
date_part = base_name.split('_')[0]


# Load the manual calibration matrix
manual_calibration_matrix = pd.read_csv('manual_calibration_matrix.csv', header=None)
manual_calibration_matrix.columns = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6']

# Define the paths
force_path = r'C:\Users\kmh\Documents\DATA\2024-5\FT\F'
voltage_path = r'C:\Users\kmh\Documents\DATA\2024-5\FT\V'

# Initialize final DataFrames to store results
final_F_matched = pd.DataFrame()
final_F_match_keys = pd.DataFrame()


# Convert date format from yyyy-mm-dd to yyyy_mm_dd
date_part_formatted = date_part.replace('-', '_')
print(f'date_part_formatted: {date_part_formatted}')

# Construct the corresponding force and voltage file names
force_file = os.path.join(force_path, f'F_{date_part_formatted}.txt')
voltage_file = os.path.join(voltage_path, f'V_{date_part_formatted}.txt')
    
# Load dataframes
rfid_df = pd.read_csv(rfid_file, dtype={'time': str})
force_df = pd.read_csv(force_file, names=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz', 't'], header=None)
voltage_df = pd.read_csv(voltage_file, names=['V1', 'V2', 'V3', 'V4', 'V5', 'V6'], header=None)
    
# Transform voltage file
F_calc = np.dot(voltage_df, manual_calibration_matrix)
F_df = pd.DataFrame(F_calc, columns=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz'])
F_df['t'] = force_df['t']

#drop the rows with NaN
F_df = F_df.dropna()

# Apply the function to the 'Time' column
F_df['datetime'] = F_df['t'].apply(defs.convert_time_force)
F_df['RFID'] = pd.NA
F_df['event'] = pd.NA
F_df['datetime'] = pd.to_datetime(F_df['datetime'], format='%Y-%m-%d %H:%M:%S:%f')

#print(F_df.dtypes)

# Trim down RFID file
#dealing with the logged 'time' column instead of epoch_time
#-1 from the logged time to match local time. 
rfid_df['time'] = pd.to_datetime(rfid_df['time'], format="%H:%M:%S:%f")
rfid_df['time'] = rfid_df['time'] - pd.to_timedelta(1, unit='h')

RFID_match = rfid_df[['id', 'status', 'time']]
RFID_match.loc[:, 'id'] = RFID_match['id'].astype(str)  # Ensure 'id' is treated as string
#RFID_match.loc[:, 'epoch_time_converted'] = RFID_match['epoch_time'].apply(convert_time_rfid)
#RFID_match['epoch_time_converted'] = pd.to_datetime(RFID_match['epoch_time_converted'], format='%Y-%m-%d %H:%M:%S:%f')
RFID_match = RFID_match[(RFID_match['id'].str.len() == 10) & (~RFID_match['id'].str.contains('?', regex=False))]
RFID_match.reset_index(drop=True, inplace=True)  # Reset the index
#print(f'RFID_match.head(5): {RFID_match.head(5)}')

F_match_keys, RFID_match_keys = defs.match_keys_preparation_0216(F_df, RFID_match)
#print(f'RFID_match_keys.dtypes: {RFID_match_keys.dtypes}')
print(f'RFID_match_keys: {RFID_match_keys.head(5)}')
#print(F_match_keys.dtypes)
print(f'F_match_keys:{F_match_keys.head(5)}' )

# Initialize a list to store current_F_valid for each iteration
all_F_thisfile = []
all_F_matchkeys_thisloop = []
start_index = 0

#reset RFID_match_keys' index to prevent KeyError
RFID_match_keys.reset_index(drop=True, inplace=True)


date_part_formatted: 2024_12_12
RFID_match_keys:    hr  min   s        rfid  status           timestamp
0   8    9  28  3B00185CB8  Arrive 1900-01-01 08:09:28
1   8    9  30  3B00185CB8  Depart 1900-01-01 08:09:30
2   8   10   0  3B00485E69  Arrive 1900-01-01 08:10:00
3   8   10   3  3B00485E69  Depart 1900-01-01 08:10:03
4   8   10   6  3B0018A99B  Arrive 1900-01-01 08:10:06
F_match_keys:   index  hr  min   s           timestamp  event  RFID
0      0   8    5  19 1900-01-01 08:05:19      1  <NA>
1   1000   8    5  20 1900-01-01 08:05:20      1  <NA>
2   2000   8    5  43 1900-01-01 08:05:43      2  <NA>
3   3000   8    6  33 1900-01-01 08:06:33      3  <NA>
4   4000   8    6  37 1900-01-01 08:06:37      4  <NA>


In [ ]:
#special joining for 2025-02-16 -> something's wrong with 2025-02-16. only one match

# Load the first .txt file into a DataFrame
df1 = pd.read_csv(r'C:\Users\kmh\Documents\DATA\2024-5\FT\V\V_2025_02_16_a.txt')  # Adjust 'delimiter' as needed
df1.columns = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6','t']

# Load the second .txt file into a DataFrame
df2 = pd.read_csv(r'C:\Users\kmh\Documents\DATA\2024-5\FT\V\V_2025_02_16_b.txt')  # Adjust 'delimiter' as needed
df2.columns = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6','t']

# Append the datasets
combined_df = pd.concat([df1, df2], ignore_index=True)
combined_df.to_csv(r'C:\Users\kmh\Documents\DATA\2024-5\FT\V\V_2025_02_16.txt',header = None, index= False)


In [ ]:
print(df1.head(5))
print(df2.head(5))
print()

      V1     V2     V3     V4     V5     V6             t
0  0.218  0.000 -0.016 -0.014 -0.211  0.006  3.822537e+09
1  0.212 -0.001 -0.015 -0.014 -0.207  0.007  3.822537e+09
2  0.208 -0.002 -0.015 -0.014 -0.205  0.006  3.822537e+09
3  0.210 -0.000 -0.014 -0.013 -0.206  0.006  3.822537e+09
4  0.214 -0.002 -0.016 -0.016 -0.211  0.006  3.822537e+09
      V1     V2     V3     V4     V5     V6             t
0  0.809 -0.062 -0.457  0.010 -0.458 -0.026  3.822545e+09
1  0.809 -0.061 -0.456  0.009 -0.460 -0.026  3.822545e+09
2  0.806 -0.061 -0.454  0.009 -0.457 -0.025  3.822545e+09
3  0.803 -0.061 -0.454  0.010 -0.455 -0.025  3.822545e+09
4  0.805 -0.061 -0.454  0.010 -0.458 -0.026  3.822545e+09


### V as timestamp

In [ ]:
import os
import glob
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from tqdm import tqdm
import warnings

warnings.filterwarnings('ignore')

# CHANGE HERE
rfid_file = r'C:\Users\kmh\Documents\DATA\2024-5\RFID\RFID\2025-02-18_RFID_RFID.csv' #this is the date I am dealing with now. 

# Extract the date from the RFID file name
base_name = os.path.basename(rfid_file)
date_part = base_name.split('_')[0]


# Load the manual calibration matrix
manual_calibration_matrix = pd.read_csv('manual_calibration_matrix.csv', header=None)
manual_calibration_matrix.columns = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6']
#manual_calibration_matrix = np.array(manual_calibration_matrix)

# Define the paths
voltage_path = r'C:\Users\kmh\Documents\DATA\2024-5\FT\V'

# Initialize final DataFrames to store results
final_F_matched = pd.DataFrame()
final_F_match_keys = pd.DataFrame()


# Convert date format from yyyy-mm-dd to yyyy_mm_dd
date_part_formatted = date_part.replace('-', '_')
print(f'date_part_formatted: {date_part_formatted}')

# Construct the corresponding force and voltage file names
voltage_file = os.path.join(voltage_path, f'V_{date_part_formatted}.txt')
    
# Load dataframes
rfid_df = pd.read_csv(rfid_file, dtype={'epoch_time': float})
voltage_df = pd.read_csv(voltage_file, names=['V1', 'V2', 'V3', 'V4', 'V5', 'V6','t'],header =None)
voltage_df1 = voltage_df[['V1','V2','V3','V4','V5','V6']]
#drop the rows with NaN

# Transform voltage file
F_calc = np.dot(voltage_df1, manual_calibration_matrix)
F_df = pd.DataFrame(F_calc, columns=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz'])
F_df['t'] = voltage_df['t']

#drop the rows with NaN
F_df = F_df.dropna()

# Apply the function to the 'Time' column
F_df['datetime'] = F_df['t'].apply(force_defs.convert_time_force)
F_df['RFID'] = pd.NA
F_df['event'] = pd.NA
F_df['datetime'] = pd.to_datetime(F_df['datetime'], format='%Y-%m-%d %H:%M:%S:%f')

#print(F_df.dtypes)

# Trim down RFID file
RFID_match = rfid_df[['id', 'status', 'epoch_time']]
RFID_match.loc[:, 'id'] = RFID_match['id'].astype(str)  # Ensure 'id' is treated as string
RFID_match.loc[:, 'epoch_time_converted'] = RFID_match['epoch_time'].apply(defs.convert_time_rfid)
RFID_match['epoch_time_converted'] = pd.to_datetime(RFID_match['epoch_time_converted'], format='%Y-%m-%d %H:%M:%S:%f')
RFID_match = RFID_match[(RFID_match['id'].str.len() == 10) & (~RFID_match['id'].str.contains('?', regex=False))]
RFID_match.reset_index(drop=True, inplace=True)  # Reset the index
#print(f'RFID_match.head(5): {RFID_match.head(5)}')

F_match_keys, RFID_match_keys = force_defs.match_keys_preparation(F_df, RFID_match)
#print(f'RFID_match_keys.dtypes: {RFID_match_keys.dtypes}')
print(f'RFID_match_keys: {RFID_match_keys.head(5)}')
#print(F_match_keys.dtypes)
print(f'F_match_keys:{F_match_keys.head(5)}' )

# Initialize a list to store current_F_valid for each iteration
all_F_thisfile = []
all_F_matchkeys_thisloop = []
start_index = 0

#reset RFID_match_keys' index to prevent KeyError
RFID_match_keys.reset_index(drop=True, inplace=True)


date_part_formatted: 2025_02_18
RFID_match_keys:    hr  min   s        rfid  status timestamp
0   8    5  56  3B00192E1E  Arrive  08:05:56
1   8    6   0  3B00192E1E  Depart  08:06:00
2   8   28  32  3B00484043  Arrive  08:28:32
3   8   28  37  3B00484043  Depart  08:28:37
4   8   33   7  3B0018C6F9  Arrive  08:33:07
F_match_keys:   index  hr  min   s timestamp  event  RFID
0      0   7   44   5  07:44:05      1  <NA>
1   1000   7   44   6  07:44:06      1  <NA>
2   2000   7   44   7  07:44:07      1  <NA>
3   3000   7   46  28  07:46:28      2  <NA>
4   4000   7   46  29  07:46:29      2  <NA>


### V as timestamp 02-16 and 02-17 specific
- epoch_time somehow incorrectly logged
- need to use 'time' column instead and -1hr from the logged time 
- hmmm should I perhaps consider using 'time' column for all the other dataset? there were surprisingly not many sample size for just first visits. When it kinda has to be near 30 x 12 = 360 
- this might be the main code as 'epoch_time' is often unreliable. 

In [4]:
import os
import glob
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from tqdm import tqdm
import warnings

warnings.filterwarnings('ignore')

# CHANGE HERE
rfid_file = r'C:\Users\kmh\Documents\DATA\2024-5\RFID\RFID\2025-02-17_RFID_RFID.csv' #this is the date I am dealing with now. 

# Extract the date from the RFID file name
base_name = os.path.basename(rfid_file)
date_part = base_name.split('_')[0]


# Load the manual calibration matrix
manual_calibration_matrix = pd.read_csv('manual_calibration_matrix.csv', header=None)
manual_calibration_matrix.columns = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6']
#manual_calibration_matrix = np.array(manual_calibration_matrix)

# Define the paths
voltage_path = r'C:\Users\kmh\Documents\DATA\2024-5\FT\V'

# Initialize final DataFrames to store results
final_F_matched = pd.DataFrame()
final_F_match_keys = pd.DataFrame()


# Convert date format from yyyy-mm-dd to yyyy_mm_dd
date_part_formatted = date_part.replace('-', '_')
print(f'date_part_formatted: {date_part_formatted}')

# Construct the corresponding force and voltage file names
voltage_file = os.path.join(voltage_path, f'V_{date_part_formatted}.txt')
    
# Load dataframes
rfid_df = pd.read_csv(rfid_file, dtype={'date':str,'time': str})
rfid_df['time'] = rfid_df['time'].astype(str).apply(lambda x: ".".join(x.rsplit(":", 1)))
rfid_df['datetime'] = rfid_df['date']+ ' '+rfid_df['time']

#
#-1hr 
#dealing with the logged 'time' column instead of epoch_time
#-1 from the logged time to match local time. 
rfid_df['datetime'] = pd.to_datetime(rfid_df['datetime'])
rfid_df['rfid_datetime'] = rfid_df['datetime'] - pd.to_timedelta(1, unit='h')

voltage_df = pd.read_csv(voltage_file, names=['V1', 'V2', 'V3', 'V4', 'V5', 'V6','t'],header =None)
voltage_df1 = voltage_df[['V1','V2','V3','V4','V5','V6']]
#drop the rows with NaN

# Transform voltage file
F_calc = np.dot(voltage_df1, manual_calibration_matrix)
F_df = pd.DataFrame(F_calc, columns=['Fx', 'Fy', 'Fz', 'Tx', 'Ty', 'Tz'])
F_df['t'] = voltage_df['t']

#drop the rows with NaN
F_df = F_df.dropna()

# Apply the function to the 'Time' column
F_df['datetime'] = F_df['t'].apply(defs.convert_time_force)
F_df['RFID'] = pd.NA
F_df['event'] = pd.NA
F_df['datetime'] = pd.to_datetime(F_df['datetime'], format='%Y-%m-%d %H:%M:%S:%f')

#print(F_df.dtypes)

# Trim down RFID file
# working with 'time'
RFID_match = rfid_df[['id', 'status', 'rfid_datetime']]
RFID_match.loc[:, 'id'] = RFID_match['id'].astype(str)  # Ensure 'id' is treated as string
#RFID_match.loc[:, 'epoch_time_converted'] = RFID_match['epoch_time'].apply(convert_time_rfid)
#RFID_match['epoch_time_converted'] = pd.to_datetime(RFID_match['epoch_time_converted'], format='%Y-%m-%d %H:%M:%S:%f')
RFID_match = RFID_match[(RFID_match['id'].str.len() == 10) & (~RFID_match['id'].str.contains('?', regex=False))]
RFID_match.reset_index(drop=True, inplace=True)  # Reset the index
#print(f'RFID_match.head(5): {RFID_match.head(5)}')

F_match_keys, RFID_match_keys = defs.match_keys_preparation(F_df, RFID_match)
#print(f'RFID_match_keys.dtypes: {RFID_match_keys.dtypes}')
print(f'RFID_match_keys: {RFID_match_keys.head(5)}')
#print(F_match_keys.dtypes)
print(f'F_match_keys:{F_match_keys.head(5)}' )

# Initialize a list to store current_F_valid for each iteration
all_F_thisfile = []
all_F_matchkeys_thisloop = []
start_index = 0

#reset RFID_match_keys' index to prevent KeyError
RFID_match_keys.reset_index(drop=True, inplace=True)


date_part_formatted: 2025_02_17
RFID_match_keys:    hr  min   s        rfid  status timestamp
0   7    3  42  3B00484043  Arrive  07:03:42
1   7    3  45  3B00484043  Depart  07:03:45
2   7    3  50  3B00484043  Arrive  07:03:50
3   7    3  52  3B00484043  Depart  07:03:52
4   7    4   0  3B00484043  Arrive  07:04:00
F_match_keys:   index  hr  min   s timestamp  event  RFID
0      0   6   53  27  06:53:27      1  <NA>
1   1000   6   53  28  06:53:28      1  <NA>
2   2000   6   53  29  06:53:29      1  <NA>
3   3000   6   53  30  06:53:30      1  <NA>
4   4000   6   53  31  06:53:31      1  <NA>


In [109]:
F_match_keys.to_csv('F_match_keys_0217.csv')
RFID_match_keys.to_csv('RFID_match_keys_0217.csv')

## c. MAIN CODE

In [17]:
# MAIN CODE 
for i in range(len(RFID_match_keys) - 1):
    if i + 1 < len(RFID_match_keys):
        if RFID_match_keys.loc[i, 'status'] == "Arrive" and RFID_match_keys.loc[i + 1, 'status'] in ["Displace", "Depart"]:
            F_match_keys_in, current_F_valid, matching_end_index = defs.assign(RFID_match_keys, F_match_keys, F_df, start_index)
            # Update start_index for the next iteration
            start_index = matching_end_index + 1000 if matching_end_index is not None else start_index

        elif RFID_match_keys.loc[i, 'status'] == "Displace" and RFID_match_keys.loc[i + 1, 'status'] == "Depart":
            F_match_keys_in, current_F_valid, matching_end_index = defs.assign(RFID_match_keys, F_match_keys, F_df, start_index)
            # Update start_index for the next iteration
            start_index = matching_end_index + 1000 if matching_end_index is not None else start_index

        if isinstance(current_F_valid, list):
            current_F_valid = pd.DataFrame(current_F_valid)

        all_F_thisfile.append(current_F_valid)

        if isinstance(F_match_keys_in, list):
            F_match_keys_in = pd.DataFrame(F_match_keys_in)

        all_F_matchkeys_thisloop.append(F_match_keys_in)

#concatenate the matches            
all_F_thisfile_df = pd.concat(all_F_thisfile, ignore_index=True)
all_F_matchkeys_this_loop_df = pd.concat(all_F_matchkeys_thisloop, ignore_index = True)

#appends per iteration? 
final_F_matched = pd.concat([final_F_matched, all_F_thisfile_df], ignore_index=True)
final_F_match_keys = pd.concat([final_F_match_keys, all_F_matchkeys_this_loop_df], ignore_index=True)

print("Final matched DataFrame:")
print(final_F_matched)

print("Final match keys DataFrame:")
print(final_F_match_keys)
#took 18m 20s for 12-12 which logged most visits and most individuals
#somehow cannot replicate the 12-12. 

Final matched DataFrame:
               Fx        Fy        Fz        Tx        Ty        Tz  \
0       -1.870222 -5.737000  1.386616 -0.040908 -0.028999 -0.000499   
1       -1.874636 -5.735134  1.384855 -0.041137 -0.029422 -0.000478   
2       -1.876605 -5.730647  1.383437 -0.041401 -0.029530 -0.000457   
3       -1.870464 -5.731841  1.384551 -0.041374 -0.029185 -0.000485   
4       -1.869198 -5.736343  1.382003 -0.041143 -0.028919 -0.000458   
...           ...       ...       ...       ...       ...       ...   
1698995 -2.219255 -5.698232  1.217253 -0.041209 -0.036836 -0.001534   
1698996 -2.217553 -5.702399  1.216387 -0.041171 -0.036735 -0.001534   
1698997 -2.215750 -5.701321  1.217780 -0.041041 -0.036619 -0.001554   
1698998 -2.217375 -5.698466  1.215635 -0.041063 -0.036697 -0.001534   
1698999 -2.218240 -5.698859  1.216529 -0.041202 -0.036836 -0.001524   

                    t                datetime        RFID  event  
0        3.816836e+09 2024-12-12 08:09:30.195  3B00185C

In [ ]:
final_F_matched.shape 
#1699000, 10 for 12-12
#2874998 for 02_16. 
#2214000 for 01_22

(1699000, 10)

In [19]:
final_F_matched['RFID'].nunique()

25

In [20]:
# Calculate the number of unique values in the 'event' column of F_match_keys_in
num_unique_events = final_F_match_keys['event'].nunique()

print(f"The number matched event is: {num_unique_events}")

#764! Halleluja


The number matched event is: 419


In [ ]:
#compare with the dataset that's already saved

In [19]:
Feb15_F_dataset = pd.read_csv('c:\\Users\\kmh\\Documents\\shed-tits\\data\\FTdata\\2025_02_15_F_matched.csv')
Feb15_F_dataset['RFID'].nunique()

31

In [ ]:
num_unique_events = Feb15_F_dataset['event'].nunique()

print(f"The number matched event is: {num_unique_events}") #ohhh different. a bit less 

The number matched event is: 397


## d. SAVE- DOUBLE CHECK!!

In [22]:
final_F_matched.to_csv('c:\\Users\\kmh\\Documents\\shed-tits\\data\\2024_12_12_F_matched.csv')
final_F_match_keys.to_csv('c:\\Users\\kmh\\Documents\\shed-tits\\data\\2024_12_12_F_matchkeys.csv')

## e. summary 

In [28]:
import pandas as pd
import os

# Define the directory containing the CSV files
data_dir = r"C:\Users\kmh\Documents\shed-tits\data\FTdata\matched_epoch"

# Initialize an empty list to store the summary rows
summary_data = []

# Loop through each CSV file in the directory
for file in os.listdir(data_dir):
    if file.endswith(".csv"):  # Only process CSV files
        file_path = os.path.join(data_dir, file)
        
        # Read the CSV file into a DataFrame
        df = pd.read_csv(file_path)
        
        # Calculate the number of unique values in 'RFID' column and the number of rows
        unique_RFIDs = df['RFID'].nunique()
        no_of_rows = len(df)
        
        # Append the results as a dictionary to the summary data list
        summary_data.append({
            'filename': file,
            'unique_RFIDs': unique_RFIDs,
            'no_of_rows': no_of_rows
        })

# Convert the list of dictionaries to a DataFrame
epoch_summary = pd.DataFrame(summary_data)

# Display the summary DataFrame
print(epoch_summary)

                    filename  unique_RFIDs  no_of_rows
0   2024_12_12_F_matched.csv            25     1699000
1   2024_12_15_F_matched.csv            21     1375000
2   2024_12_23_F_matched.csv            24     2260000
3   2024_12_31_F_matched.csv            16      816000
4   2025_01_03_F_matched.csv            19      863000
5   2025_01_21_F_matched.csv            22     1295000
6   2025_01_24_F_matched.csv            30     1769000
7   2025_01_30_F_matched.csv            20      510000
8   2025_02_06_F_matched.csv            29      984000
9   2025_02_12_F_matched.csv            45     4231000
10  2025_02_16_F_matched.csv            41     2874998
11  2025_02_19_F_matched.csv            39     2376000
